In [11]:
label_to_coordinates = {
    "1-1": (0, 0), "1-2": (0.6, 0), "1-3": (1.2, 0), "1-4": (1.8, 0), "1-5": (2.4, 0), "1-6": (3.0, 0),"1-7": (3.6, 0), "1-8": (4.2, 0), "1-9": (4.8, 0), "1-10": (5.4, 0), "1-11": (6.0, 0),
    "2-1": (0, 0.6), "2-11": (6.0, 0.6),
    "3-1": (0, 1.2), "3-11": (6.0, 1.2),
    "4-1": (0, 1.8), "4-11": (6.0, 1.8),
    "5-1": (0, 2.4), "5-11": (6.0, 2.4),
    "6-1": (0, 3.0), "6-2": (0.6, 3.0), "6-3": (1.2, 3.0), "6-4": (1.8, 3.0), "6-5": (2.4, 3.0),"6-6": (3.0, 3.0), "6-7": (3.6, 3.0), "6-8": (4.2, 3.0), "6-9": (4.8, 3.0), "6-10": (5.4, 3.0), "6-11": (6.0, 3.0),
    "7-1": (0, 3.6), "7-11": (6.0, 3.6),
    "8-1": (0, 4.2), "8-11": (6.0, 4.2),
    "9-1": (0, 4.8), "9-11": (6.0, 4.8),
    "10-1": (0, 5.4), "10-11": (6.0, 5.4),
    "11-1": (0, 6.0), "11-2": (0.6, 6.0), "11-3": (1.2, 6.0), "11-4": (1.8, 6.0), "11-5": (2.4, 6.0),"11-6": (3.0, 6.0), "11-7": (3.6, 6.0), "11-8": (4.2, 6.0), "11-9": (4.8, 6.0), "11-10": (5.4, 6.0), "11-11": (6.0, 6.0)
}
label_mapping = {
    '11': '1-1','10': '1-2','9': '1-3','8': '1-4','7': '1-5','6': '1-6','5': '1-7','4': '1-8','3': '1-9','2': '1-10','1': '1-11',
    '12': '2-1','30': '2-11',
    '13': '3-1','29': '3-11',
    '14': '4-1','28': '4-11',
    '15': '5-1','27': '5-11',
    '16': '6-1','17': '6-2','18': '6-3','19': '6-4','20': '6-5','21': '6-6','22': '6-7','23': '6-8','24': '6-9','25': '6-10','26': '6-11',
    '49': '7-1','31': '7-11',
    '48': '8-1','32': '8-11',
    '47': '9-1','33': '9-11',
    '46': '10-1','34': '10-11',
    '45': '11-1','44': '11-2','43': '11-3','42': '11-4','41': '11-5','40': '11-6','39': '11-7','38': '11-8','37': '11-9','36': '11-10','35': '11-11'
}

In [12]:
import pandas as pd
import numpy as np
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler
from tensorflow.keras.models import load_model
from tensorflow import keras
import tensorflow as tf
import joblib  # 用於保存模型
import json
from sklearn.model_selection import train_test_split

from sklearn.model_selection import StratifiedShuffleSplit
import time
from tensorflow.keras.callbacks import EarlyStopping
from sklearn.linear_model import SGDRegressor

In [13]:
selected_columns = ['Label',
                    'AP1_Distance (mm)','AP2_Distance (mm)','AP3_Distance (mm)',
                    'AP1_StdDev (mm)','AP2_StdDev (mm)','AP3_StdDev (mm)',
                    'AP1_Rssi', 'AP2_Rssi', 'AP3_Rssi', 'AP4_Rssi']  

scaler_columns = [  'AP1_Distance (mm)','AP2_Distance (mm)','AP3_Distance (mm)',
                    'AP1_StdDev (mm)','AP2_StdDev (mm)','AP3_StdDev (mm)',
                  'AP1_Rssi', 'AP2_Rssi', 'AP3_Rssi', 'AP4_Rssi',
                  'AP4_Distance_predicted']

label_column = 'Label'
target_column = 'Label'


#  'AP1_Rssi','AP2_Rssi','AP3_Rssi','AP4_Rssi'
# 'AP1_Distance (mm)','AP2_Distance (mm)','AP3_Distance (mm)','AP4_Distance (mm)',
# 'AP1_StdDev (mm)','AP2_StdDev (mm)','AP3_StdDev (mm)','AP4_StdDev (mm)',

In [14]:
dataamount_set = [1,10,40]
N_val_set = [0,2,8]

In [15]:
for dada in range(3):

    dataamount = dataamount_set[dada]
    N_val = N_val_set[dada]

    N_train = dataamount # 訓練集每個類別至少要有 N_train 筆資料
    test_val_ratio = 1  # 剩餘資料中，50% 作為驗證集，50% 作為測試集

    weekrepresent = [['0','0'],['0','1'],['1','2'],['2','3'],['3','4'],['4','5']]
    alldatadate = ['2024_12_21','2024_12_27','2025_01_03','2025_01_10','2025_02_28']
    number_of_week = len(alldatadate)

    ALL_model_loss = []
    ALL_model_accuracy = []
    ALL_model_mean_mde = []


    for mmm in range(10):

        ALL_trainingtime = []
        ALL_loss = []
        ALL_accuracy = []
        ALL_mean_mde = []

        for i in range(number_of_week):
            
            # 這個是 DNN input 之前的 feature vector 的 scaler
            scaler = joblib.load(f'finetune\\scaler_regressor_dnn_AP1&AP4_{mmm}.pkl')

            # 這邊是 load base model 的 regressor 和 DNN model 還需要 load regressor input 的 scaler
            if i == 0:
                base_model_reg = joblib.load(f'finetune\\regressor_model_AP1&AP4_{mmm}.pkl')
                base_model_dnn = load_model(f'finetune\\regressor_dnn_AP1&AP4_{mmm}.h5')
                base_reg_scaler = joblib.load(f'finetune\\scaler_regressor_input_{mmm}.pkl')

            else: 
                # 儲存更新後的regressor and dnn model
                base_model_reg = joblib.load(f'finetune\\regressor_model_{weekrepresent[i][0]}to{weekrepresent[i][1]}_{mmm}.pkl')
                base_model_dnn = load_model(f'finetune\\regressor_dnn_{weekrepresent[i][0]}to{weekrepresent[i][1]}_{mmm}.h5')
        

            # load data
            test_file_path = f"timestamp_allignment_Balanced_{alldatadate[i]}_rtt_logs.csv"  
            date_test = f"{alldatadate[i]}"
            data = pd.read_csv(test_file_path, usecols=selected_columns)


            # DNN transfer learnging 凍結所有層
            for layer in base_model_dnn.layers[:-1]:  # 除了最後一層 (Output Layer)
                layer.trainable = False

            # 確認哪些層可訓練
            base_model_dnn.summary()

            base_model_dnn.compile(optimizer=keras.optimizers.Adam(learning_rate=0.001),
                        loss='sparse_categorical_crossentropy',
                        metrics=['accuracy'])
            

            


            data_imputed = data.groupby(label_column).apply(
                lambda group: group.fillna(group.mean())
            ).reset_index()

            print("original data columns :")
            print(data_imputed.columns)


            reverse_label_mapping = {v: int(k) - 1 for k, v in label_mapping.items()}  # 讓數字標籤 -1

            y = data_imputed[target_column]

            y_numeric = y.map(reverse_label_mapping)
            y_numeric

            # 把label部分拿掉
            X = data_imputed.drop(columns=['level_1','Label'])

            # 轉為 DataFrame 方便操作
            data = pd.DataFrame(X)
            data['label'] = y_numeric  # 加入 label 欄位

            testing_data_full = data.groupby('label', group_keys=False).sample(n=100, replace=False, random_state=42) # 
            train_data_full = data.groupby('label', group_keys=False).sample(n=N_train, replace=False, random_state=42)
            

            if N_val > 0:
                sss = StratifiedShuffleSplit(n_splits=1, test_size=N_val / N_train) # , random_state=42
                train_index, val_index = next(sss.split(train_data_full.drop(columns=['label']), train_data_full['label']))
                train_data = train_data_full.iloc[train_index]
                val_data = train_data_full.iloc[val_index]
                
            else:
                val_data = pd.DataFrame(columns=data.columns)  # 若沒有 validation data，建立空 DataFrame
                train_data = train_data_full

            # # 剩下的資料（未被抽入 train_data_full 的部分）直接作為 test set
            # remaining_data = data.drop(train_data_full.index)
            # train_data

            # 訓練 regressor 並儲存
            ap1_data = train_data[['AP1_Rssi', 'AP1_Distance (mm)']].dropna().rename(
                columns={'AP1_Rssi': 'Rssi', 'AP1_Distance (mm)': 'Distance'}
            )

            ap2_data = train_data[['AP2_Rssi', 'AP2_Distance (mm)']].dropna().rename(
                columns={'AP2_Rssi': 'Rssi', 'AP2_Distance (mm)': 'Distance'}
            )

            ap3_data = train_data[['AP3_Rssi', 'AP3_Distance (mm)']].dropna().rename(
                columns={'AP3_Rssi': 'Rssi', 'AP3_Distance (mm)': 'Distance'}
            )

            # ap4_data = train_data[['AP4_Rssi', 'AP4_Distance (mm)']].dropna().rename(
            #     columns={'AP4_Rssi': 'Rssi', 'AP4_Distance (mm)': 'Distance'}
            # )

            train_data_reg = pd.concat([ap1_data,ap2_data,ap3_data], ignore_index=True)


            X_train_reg = train_data_reg[['Rssi']]
            y_train_reg = train_data_reg['Distance']

            X_train_reg_scaled = base_reg_scaler.transform(X_train_reg)

            # 重新訓練模型（fine tuning）
            model_reg_finetuned = base_model_reg
            model_reg_finetuned.partial_fit(X_train_reg_scaled, y_train_reg)

            # 檢查更新後的係數與截距
            print("更新後模型的係數：", model_reg_finetuned.coef_, "截距：", model_reg_finetuned.intercept_)

            

            ### train data
            # train_data['AP1_Distance_predicted'] = np.nan
            # train_data['AP2_Distance_predicted'] = np.nan
            # train_data['AP3_Distance_predicted'] = np.nan
            train_data['AP4_Distance_predicted'] = np.nan

            # mask_ap1 = train_data['AP1_Rssi'].notna()
            # train_data.loc[mask_ap1, 'AP1_Distance_predicted'] = model_reg_finetuned.predict(
            #     train_data.loc[mask_ap1, ['AP1_Rssi']].rename(columns={'AP1_Rssi': 'Rssi'})
            # )

            # # 利用 AP2_Rssi 預測 AP2_Distance_predicted
            # mask_ap2 = train_data['AP2_Rssi'].notna()
            # if mask_ap2.any():
            #     # 先將 AP2_Rssi 轉換成 regressor 所需的格式並標準化
            #     AP2_Rssi_scaled = base_reg_scaler.transform(train_data.loc[mask_ap2, ['AP2_Rssi']].rename(columns={'AP2_Rssi': 'Rssi'}))
            #     train_data.loc[mask_ap2, 'AP2_Distance_predicted'] = model_reg_finetuned.predict(AP2_Rssi_scaled)
    
            # # 利用 AP3_Rssi 預測 AP3_Distance_predicted
            # mask_ap3 = train_data['AP3_Rssi'].notna()
            # if mask_ap3.any():
            #     AP3_Rssi_scaled = base_reg_scaler.transform(train_data.loc[mask_ap3, ['AP3_Rssi']].rename(columns={'AP3_Rssi': 'Rssi'}))
            #     train_data.loc[mask_ap3, 'AP3_Distance_predicted'] = model_reg_finetuned.predict(AP3_Rssi_scaled)

            mask_ap4 = train_data['AP4_Rssi'].notna()
            train_data.loc[mask_ap4, 'AP4_Distance_predicted'] = model_reg_finetuned.predict(
                train_data.loc[mask_ap4, ['AP4_Rssi']].rename(columns={'AP4_Rssi': 'Rssi'})
            )

            if N_val > 0:
                ### val data
                # val_data['AP1_Distance_predicted'] = np.nan
                # val_data['AP2_Distance_predicted'] = np.nan
                # val_data['AP3_Distance_predicted'] = np.nan
                val_data['AP4_Distance_predicted'] = np.nan

                # mask_ap1 = val_data['AP1_Rssi'].notna()
                # val_data.loc[mask_ap1, 'AP1_Distance_predicted'] = model_reg_finetuned.predict(
                #     val_data.loc[mask_ap1, ['AP1_Rssi']].rename(columns={'AP1_Rssi': 'Rssi'})
                # )

                # # 利用 AP2_Rssi 預測 AP2_Distance_predicted
                # mask_ap2 = val_data['AP2_Rssi'].notna()
                # if mask_ap2.any():
                #     # 先將 AP2_Rssi 轉換成 regressor 所需的格式並標準化
                #     AP2_Rssi_scaled = base_reg_scaler.transform(val_data.loc[mask_ap2, ['AP2_Rssi']].rename(columns={'AP2_Rssi': 'Rssi'}))
                #     val_data.loc[mask_ap2, 'AP2_Distance_predicted'] = model_reg_finetuned.predict(AP2_Rssi_scaled)
        
                # # # 利用 AP3_Rssi 預測 AP3_Distance_predicted
                # mask_ap3 = val_data['AP3_Rssi'].notna()
                # if mask_ap3.any():
                #     AP3_Rssi_scaled = base_reg_scaler.transform(val_data.loc[mask_ap3, ['AP3_Rssi']].rename(columns={'AP3_Rssi': 'Rssi'}))
                #     val_data.loc[mask_ap3, 'AP3_Distance_predicted'] = model_reg_finetuned.predict(AP3_Rssi_scaled)

                mask_ap4 = val_data['AP4_Rssi'].notna()
                val_data.loc[mask_ap4, 'AP4_Distance_predicted'] = model_reg_finetuned.predict(
                    val_data.loc[mask_ap4, ['AP4_Rssi']].rename(columns={'AP4_Rssi': 'Rssi'})
                )

            ### remaining data
            # testing_data_full['AP1_Distance_predicted'] = np.nan
            # testing_data_full['AP2_Distance_predicted'] = np.nan
            # testing_data_full['AP3_Distance_predicted'] = np.nan
            testing_data_full['AP4_Distance_predicted'] = np.nan

            
            # mask_ap1 = testing_data_full['AP1_Rssi'].notna()
            # testing_data_full.loc[mask_ap1, 'AP1_Distance_predicted'] = model_reg_finetuned.predict(
            #     testing_data_full.loc[mask_ap1, ['AP1_Rssi']].rename(columns={'AP1_Rssi': 'Rssi'})
            # )

            # # 利用 AP2_Rssi 預測 AP2_Distance_predicted
            # mask_ap2 = testing_data_full['AP2_Rssi'].notna()
            # if mask_ap2.any():
            #     # 先將 AP2_Rssi 轉換成 regressor 所需的格式並標準化
            #     AP2_Rssi_scaled = base_reg_scaler.transform(testing_data_full.loc[mask_ap2, ['AP2_Rssi']].rename(columns={'AP2_Rssi': 'Rssi'}))
            #     testing_data_full.loc[mask_ap2, 'AP2_Distance_predicted'] = model_reg_finetuned.predict(AP2_Rssi_scaled)
    
            # # # 利用 AP3_Rssi 預測 AP3_Distance_predicted
            # mask_ap3 = testing_data_full['AP3_Rssi'].notna()
            # if mask_ap3.any():
            #     AP3_Rssi_scaled = base_reg_scaler.transform(testing_data_full.loc[mask_ap3, ['AP3_Rssi']].rename(columns={'AP3_Rssi': 'Rssi'}))
            #     testing_data_full.loc[mask_ap3, 'AP3_Distance_predicted'] = model_reg_finetuned.predict(AP3_Rssi_scaled)

            mask_ap4 = testing_data_full['AP4_Rssi'].notna()
            testing_data_full.loc[mask_ap4, 'AP4_Distance_predicted'] = model_reg_finetuned.predict(
                testing_data_full.loc[mask_ap4, ['AP4_Rssi']].rename(columns={'AP4_Rssi': 'Rssi'})
            )

            # 更新 DNN 模型用的特徵欄位，將 regressor 預測值加入
            # selected_columns_dnn = selected_columns + ['AP1_Distance_predicted', 'AP4_Distance_predicted']

            print("new added feature column: ")
            print(list(train_data.columns))

            # -------------------------------
            # 準備 DNN 模型的輸入
            # 這邊重點：保留 DataFrame 結構，依據 scaler_columns 選取正確欄位，再進行 scaler.transform
            # -------------------------------
            # 選取訓練、驗證、測試集中的 scaler_columns（順序需與訓練時一致）

            X_train_df = train_data[scaler_columns].copy()
            y_train = train_data['label'].values
            print(X_train_df)

            if N_val > 0:
                X_val_df = val_data[scaler_columns].copy()
                y_val = val_data['label'].values

            X_test_df = testing_data_full[scaler_columns].copy()
            y_test = testing_data_full['label'].values

            # 使用預先訓練的 scaler 進行標準化
            X_scaled_train = scaler.transform(X_train_df)
            if N_val > 0: X_scaled_val = scaler.transform(X_val_df)
            X_scaled_test = scaler.transform(X_test_df)

            # print("訓練資料數量：", len(X_scaled_train))
            # print("驗證資料數量：", len(X_scaled_val))
            # print("測試資料數量：", len(X_scaled_test))


            # **轉換為 NumPy 陣列**
            X_train, y_train = train_data.drop(columns=['label']).values, train_data['label'].values
            X_val, y_val = val_data.drop(columns=['label']).values, val_data['label'].values
            X_test, y_test = testing_data_full.drop(columns=['label']).values, testing_data_full['label'].values


            # **計算每個 Set 內各 Label 的資料數量**
            train_label_counts = pd.Series(y_train).value_counts().sort_index()
            val_label_counts = pd.Series(y_val).value_counts().sort_index()
            test_label_counts = pd.Series(y_test).value_counts().sort_index()

            # **確保所有 Labels 都有出現在三個 Set 裡**
            all_labels = sorted(set(train_label_counts.index) | set(val_label_counts.index) | set(test_label_counts.index))
            label_distribution = pd.DataFrame(index=all_labels)

            label_distribution["Training Set"] = train_label_counts
            label_distribution["Validation Set"] = val_label_counts
            label_distribution["Test Set"] = test_label_counts

            # **用 0 填補缺失值（表示該 Label 在該 Set 中沒有數據）**
            label_distribution = label_distribution.fillna(0).astype(int)

            from IPython.display import display
            display(label_distribution)

            start_time = time.time()

            if N_val > 0:
                early_stop = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)
                base_model_dnn.fit(X_scaled_train, y_train,
                                validation_data=(X_scaled_val, y_val),
                                epochs=10000, batch_size=min(32, max(8, len(X_scaled_train) // 2)),
                                callbacks=[early_stop])
            else:
                early_stop = EarlyStopping(monitor='loss', patience=10, restore_best_weights=True)
                base_model_dnn.fit(X_scaled_train, y_train,
                                epochs=10000, batch_size=min(32, max(8, len(X_scaled_train) // 2)),
                                callbacks=[early_stop])

            end_time = time.time()

            training_time = end_time - start_time
            # print(f"訓練時間：{training_time:.2f} 秒")
            

            # Accuracy
            loss, accuracy = base_model_dnn.evaluate(X_scaled_test, y_test)
            # print(f"Evaluation on 90% unused data - Loss: {loss:.4f}, Accuracy: {accuracy:.4f}")


        # MDE
            # 預測測試資料
            y_test_pred_numeric = base_model_dnn.predict(X_scaled_test)
            y_pred_classes = np.argmax(y_test_pred_numeric, axis=1)

            # 轉換為原本的 Label
            y_test_pred_labels = [label_mapping[str(num + 1)] for num in y_pred_classes]  # 補回 +1

            # 讀取測試資料的實際 Label
            y_test_actual = [label_mapping[str(num + 1)] for num in y_test]  # 補回 +1

            # 取得預測與實際座標
            y_test_pred_coordinates = np.array([label_to_coordinates[label] for label in y_test_pred_labels])
            y_test_actual_coordinates = np.array([label_to_coordinates[label] for label in y_test_actual])

            # 計算 MDE (Mean Distance Error)
            distances = np.linalg.norm(y_test_pred_coordinates - y_test_actual_coordinates, axis=1)
            mean_mde = np.mean(distances)

            # 記錄每個 RP 的 MDE
            mde_report_test = {}
            for true_label, distance in zip(y_test_actual, distances):
                if true_label not in mde_report_test:
                    mde_report_test[true_label] = []
                mde_report_test[true_label].append(distance)

            # 計算測試資料的 MDE 平均值
            mde_report_test_avg = {label: {"mde": np.mean(dists), "count": len(dists)} for label, dists in mde_report_test.items()}


            # 儲存更新後的regressor and dnn model
            joblib.dump(model_reg_finetuned,f'finetune\\regressor_model_{weekrepresent[i+1][0]}to{weekrepresent[i+1][1]}_{mmm}.pkl')
            base_model_dnn.save(f'finetune\\regressor_dnn_{weekrepresent[i+1][0]}to{weekrepresent[i+1][1]}_{mmm}.h5')

        
            # 內層迴圈結束後，只存這一次的最佳結果
            # ALL_trainingtime.append()
            ALL_mean_mde.append(mean_mde)
            ALL_loss.append(loss)
            ALL_accuracy.append(accuracy)

        ALL_model_accuracy.append(ALL_accuracy)
        ALL_model_loss.append(ALL_loss)
        ALL_model_mean_mde.append(ALL_mean_mde)

    output_lines = []

    # 印出每個模型
    for count, (m, n, p) in enumerate(zip(ALL_model_loss, ALL_model_accuracy, ALL_model_mean_mde)):
        output_lines.append(f"model_{count}")

        output_lines.append("Loss")
        line = "[" + ", ".join(f"{l:.4f}" for l in m) + "]"
        output_lines.append(line)

        output_lines.append("Accuracy")
        line = "[" + ", ".join(f"{a:.4f}" for a in n) + "]"
        output_lines.append(line)

        output_lines.append("MDE")
        line = "[" + ", ".join(f"{sasa:.4f}" for sasa in p) + "]"
        output_lines.append(line)

        output_lines.append(" ")  # 空行

    # 計算平均
    loss_arr = np.array(ALL_model_loss)
    acc_arr = np.array(ALL_model_accuracy)
    mde_arr = np.array(ALL_model_mean_mde)

    loss_avg = np.mean(loss_arr, axis=0)
    acc_avg = np.mean(acc_arr, axis=0)
    mde_avg = np.mean(mde_arr, axis=0)

    output_lines.append("Average Loss")
    output_lines.append("[" + ", ".join(f"{v:.4f}" for v in loss_avg) + "]")

    output_lines.append("Average Accuracy")
    output_lines.append("[" + ", ".join(f"{v:.4f}" for v in acc_avg) + "]")

    output_lines.append("Average MDE")
    output_lines.append("[" + ", ".join(f"{v:.4f}" for v in mde_avg) + "]")

    # 印出到螢幕
    for line in output_lines:
        print(line)

    # 存檔到文字檔
    with open(f"finetune\\RegDNN 3mcAP worst {dataamount} data per RP fine tune.txt", "w") as f:
        for line in output_lines:
            f.write(line + "\n")



Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ dense (Dense)                   │ (None, 128)            │         1,536 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization             │ (None, 128)            │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 256)            │        33,024 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_1           │ (None, 256)            │         1,024 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 128)            │        32,896 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_2           │ (None, 128)            │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_3 (Dense)                 │ (None, 49)             │         6,321 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 75,827 (296.20 KB)

 Trainable params: 6,321 (24.69 KB)

 Non-trainable params: 69,504 (271.50 KB)

...

original data columns :
Index(['Label', 'level_1', 'AP1_Distance (mm)', 'AP2_Distance (mm)',
       'AP3_Distance (mm)', 'AP1_Rssi', 'AP2_Rssi', 'AP3_Rssi', 'AP4_Rssi',
       'AP1_StdDev (mm)', 'AP2_StdDev (mm)', 'AP3_StdDev (mm)'],
      dtype='object')
更新後模型的係數： [-539.24092511] 截距： [3391.44845153]
new added feature column: 
['AP1_Distance (mm)', 'AP2_Distance (mm)', 'AP3_Distance (mm)', 'AP1_Rssi', 'AP2_Rssi', 'AP3_Rssi', 'AP4_Rssi', 'AP1_StdDev (mm)', 'AP2_StdDev (mm)', 'AP3_StdDev (mm)', 'label', 'AP4_Distance_predicted']
       AP1_Distance (mm)  AP2_Distance (mm)  AP3_Distance (mm)  \
14895             3491.0             3569.0             -108.0   
19755             1655.0             5171.0             5946.0   
15895             3413.0             4907.0              789.0   
2944               600.0            12231.0             2772.0   
2728              2866.0             7485.0              545.0   
...                  ...                ...                ...   
17416

C:\Users\吳定洋\AppData\Local\Temp\ipykernel_6244\201025234.py:141: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_data['AP4_Distance_predicted'] = np.nan
c:\Users\吳定洋\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\base.py:486: UserWarning: X has feature names, but SGDRegressor was fitted without feature names
  warnings.warn(
C:\Users\吳定洋\AppData\Local\Temp\ipykernel_6244\201025234.py:171: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  val_data['AP4_Distance_predicted'] = np.nan
c:\User

Training Set  Validation Set  Test Set
0             32               8       100
1             32               8       100
2             32               8       100
3             32               8       100
4             32               8       100
5             32               8       100
6             32               8       100
7             32               8       100
8             32               8       100
9             32               8       100
10            32               8       100
11            32               8       100
12            32               8       100
13            32               8       100
14            32               8       100
15            32               8       100
16            32               8       100
17            32               8       100
18            32               8       100
19            32               8       100
20            32               8       100
21            32               8       100
22            32               8       100
23            32               8       100
24            32               8       100
25            32               8       100
26            32               8       100
27            32               8       100
28            32               8       100
29            32               8       100
30            32               8       100
31            32               8       100
32            32               8       100
33            32               8       100
34            32               8       100
35            32               8       100
36            32               8       100
37            32               8       100
38            32               8       100
39            32               8       100
40            32               8       100
41            32               8       100
42            32               8       100
43            32               8       100
44            32               8       100
45            32               8       100
46            32               8       100
47            32               8       100
48            32               8       100

Epoch 1/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step - accuracy: 0.2747 - loss: 4.6558 - val_accuracy: 0.4388 - val_loss: 2.5503
Epoch 2/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.3620 - loss: 3.0809 - val_accuracy: 0.5816 - val_loss: 1.5018
Epoch 3/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.4715 - loss: 2.1298 - val_accuracy: 0.7423 - val_loss: 0.9333
Epoch 4/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.5809 - loss: 1.5700 - val_accuracy: 0.8393 - val_loss: 0.6183
Epoch 5/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.6755 - loss: 1.1187 - val_accuracy: 0.8878 - val_loss: 0.4429
Epoch 6/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.7165 - loss: 0.9647 - val_accuracy: 0.9082 - val_loss: 0.3220
Epoch 7/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.7073 - loss: 0.9262 - val_accuracy: 0.9311 - val_loss: 0.2523
Epoch 8/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.8167 - loss: 0.6128 - val_accu

model_0
Loss
[0.0446, 0.0486, 0.0456, 0.0422, 0.0475]
Accuracy
[0.9910, 0.9890, 0.9898, 0.9892, 0.9890]
MDE
[0.0157, 0.0164, 0.0142, 0.0181, 0.0204]
 
model_1
Loss
[0.0581, 0.0427, 0.0499, 0.0510, 0.0411]
Accuracy
[0.9876, 0.9906, 0.9894, 0.9882, 0.9906]
MDE
[0.0220, 0.0150, 0.0158, 0.0204, 0.0173]
 
model_2
Loss
[0.0681, 0.0452, 0.0473, 0.0556, 0.0450]
Accuracy
[0.9843, 0.9876, 0.9898, 0.9882, 0.9888]
MDE
[0.0267, 0.0175, 0.0152, 0.0174, 0.0213]
 
model_3
Loss
[0.0481, 0.0431, 0.0524, 0.0451, 0.0350]
Accuracy
[0.9890, 0.9894, 0.9886, 0.9910, 0.9924]
MDE
[0.0190, 0.0147, 0.0207, 0.0137, 0.0140]
 
model_4
Loss
[0.0485, 0.0438, 0.0531, 0.0534, 0.0389]
Accuracy
[0.9902, 0.9894, 0.9886, 0.9888, 0.9912]
MDE
[0.0172, 0.0154, 0.0186, 0.0170, 0.0147]
 
model_5
Loss
[0.0500, 0.0367, 0.0450, 0.0460, 0.0447]
Accuracy
[0.9898, 0.9920, 0.9902, 0.9900, 0.9894]
MDE
[0.0183, 0.0120, 0.0159, 0.0140, 0.0178]
 
model_6
Loss
[0.0469, 0.0573, 0.0639, 0.0619, 0.0463]
Accuracy
[0.9894, 0.9886, 0.9892, 0.9888